In [3]:
import re
import numpy as np
import pandas as pd
from keras.models import *
from keras.layers import *
from keras.layers import *
from keras import optimizers
from keras.utils import np_utils
from keras.callbacks import TensorBoard
from keras.models import load_model
import math
import os.path
from keras.optimizers import *

Using TensorFlow backend.


/Users/Zizy/anaconda/envs/tensorflow/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: compiletime version 3.6 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.5
  return f(*args, **kwds)


In [4]:
reg = "(.*) (.*) (.*)\@(.*)\^(.*)\-(.*)\+(.*)\=(.*)\_(.*)\%(.*)\^(.*)\_(.*)\~(.*)\-(.*)\!(.*)\[(.*)\$(.*)\](.*)/A:(.*)\-(.*)\-(.*)\@(.*)\~(.*)/B:(.*)\_(.*)\_(.*)\@(.*)\|(.*)/C:(.*)\+(.*)\+(.*)\@(.*)\&(.*)/D:(.*)\!(.*)\#(.*)\$(.*)\%(.*)\|(.*)\&(.*)\;(.*)\-(.*)/E:(.*)\](.*)\^(.*)\=(.*)\~(.*)\!(.*)\@(.*)\#(.*)\+(.*)\](.*)\$(.*)\|(.*)\[(.*)\&(.*)\](.*)\=(.*)\^(.*)\~(.*)\#(.*)\_(.*)\;(.*)\$(.*)\&(.*)\%(.*)\[(.*)\|(.*)\](.*)\-(.*)\^(.*)\+(.*)\~(.*)\=(.*)\@(.*)\$(.*)\!(.*)\%(.*)\#(.*)\|(.*)\|(.*)\-(.*)\&(.*)\&(.*)\+(.*)\[(.*)\;(.*)\](.*)\;(.*)\~(.*)\~(.*)\^(.*)\^(.*)\@(.*)\[(.*)\#(.*)\=(.*)\!(.*)\~(.*)\+(.*)\!(.*)\^(.*)/F:(.*)\#(.*)\#(.*)\-(.*)\$(.*)\$(.*)\+(.*)\%(.*)\;(.*)/G:(.*)\_(.*)/H:(.*)\_(.*)/I:(.*)\_(.*)/J:(.*)\~(.*)\@(.*)"
pitches = ['xx']+[pitch + str(i) for i in range(1,8) for pitch in ["C", "Db", "D", "Eb", "E", "F", "Gb", "G", "Ab", "A", "Bb", "B"]]
phonemes = ['xx','pau'] + ["b", "p", "m", "f", "d", "t", "n", "l", "g", "k", "h", "j", "q", "x", "zh", "ch", "sh", "r", "z", "c", "s",
            "i", "u", "v", "a", "o", "e", "ai", "ei", "ao", "ou", "an", "en", "ang", "eng", "ong", "ia", "ua", "uo",
            "ie", "ve", "uai", "uei", "iao", "iou", "ian", "uan", "van", "in", "uen", "vn", "iang", "uang", "ing",
            "ueng", "iong", "er"]
local_path='/Users/Zizy/Programming/HKU/Dissertation/'
lbl_name = ['t0','t1']+['p' + str(i) for i in range(4)]
num_of_sp = 513
num_of_features=179


In [56]:
from pypinyin import pinyin, lazy_pinyin, Style
pinyin('你好吗',style=Style.NORMAL)



[['ni'], ['hao'], ['ma']]

In [43]:
w = "jin"

i = 0
j = 1
while True:

    if phos.count(w[i:j]) > 0 and j <= len(w):
        j += 1
    else:
        sub = w[i:j-1]
        print(sub)
        print(i,j-1)
        # print(j)
        i = j-1
        j = i +1 

    if i >= len(w):
        break


j
0 1
i
1 2
n
2 3


In [21]:
phos.count("ji")

0

In [52]:
len(["b", "p", "m", "f", "d", "t", "n   ", "l", "g", "k", "h", "j", "q", "x", "zh", "ch", "sh", "r", "z", "c", "s",
            "i", "u", "v", "a", "o", "e", "ai", "ei", "ao", "ou", "an", "en", "ang", "eng", "ong","ia", "ua", "uo",
            "ie", "ve", "uai", "uei", "iao", "iou", "ian", "uan", "van", "in", "un", "vn", "iang", "uang", "ing",
            "ueng", "iong"])

56

In [43]:
# read labs
def read_cn_labs():
    params_list = []
    for file_index in range(71): 
        if not os.path.isfile(local_path + 'cn_songs/lab/{:0>2d}.txt'.format(file_index)):
            continue
        params_list.append([])
        with open(local_path + 'cn_songs/lab/{:0>2d}.txt'.format(file_index), 'r+') as f:
            lines = f.readlines()
            pre_pho = None
            for index, line in enumerate(lines):
                reg = "(.*) (.*) (.*) (.*)"
                line = re.findall(reg, line)
                if (len(line)==0): 
                    continue
                else:
                    line=line[0]
                param = {'t0': line[0],
                         't1': line[1],
                         'cur_pho': line[2],
                         'pre_pho': pre_pho if pre_pho is not None else 'xx',
                         'pos': line[3]}
                pre_pho = line[2]
                params_list[-1].append(param)
            
            for index, line in enumerate(params_list[-1]):
                    if index == len(params_list[-1])-1:
                        params_list[-1][index]['next_pho']='xx'
                    else:
                        params_list[-1][index]['next_pho']=params_list[-1][index+1]['cur_pho']
               
    return np.array(params_list)


def make_one_hot(data1, size):
    data1 = np.array(data1)
    return (np.arange(size) == data1[:, None]).astype(np.integer)


def make_class(data, classes):
    result = []
    for p in data:
        result.append(classes.index(p))
    return result


def get_params_by_name(name, params_list):
    return [params[name] for params in params_list]


def convert_params_to_one_hot(name, classes, params_list):
    data = get_params_by_name(name, params_list)
    data = make_class(data, classes)
    data = make_one_hot(data, len(classes))
    return data


def feature_expend(labs):
    modified_labs = []
    for index, lab_file in enumerate(labs):
        modified_labs.append([])
        max_time_stamp = int(lab_file[-1]["t1"])
        # max_time_stamp = ms
        f0_size = int(math.ceil((max_time_stamp / 5)) + 1)
        sample_index = 0
        for sample in range(0, f0_size):
            try:
                if int(lab_file[sample_index]["t1"]) / 5 > sample:
                    modified_labs[index].append(lab_file[sample_index])
                else:
                    if len(lab_file) > sample_index + 1:
                        sample_index += 1
                    modified_labs[index].append(lab_file[sample_index])
            except:
                print(index,lab_file[sample_index])
        
    return modified_labs


def sp_feature_extract(labs):
    stacked_labs_with_feature = []
    feature_num = 0

    temp = []
    for index,lab in enumerate(labs):
        temp.append(len(lab))
    max_sample_size = max(temp)
    print("max sample size: %s" % max_sample_size)

    
    for index,lab in enumerate(labs):
        params_phonemes_one_hot = convert_params_to_one_hot('cur_pho', phonemes, lab)
        params_phonemes_pre_one_hot = convert_params_to_one_hot('pre_pho', phonemes, lab)
        params_phonemes_next_one_hot = convert_params_to_one_hot('next_pho', phonemes, lab)
        params_phonemes_position = get_params_by_name('pos', lab)

        stacked_feature = np.hstack([params_phonemes_one_hot,
                                     params_phonemes_pre_one_hot,
                                     params_phonemes_next_one_hot,
                                     np.reshape(params_phonemes_position, (len(params_phonemes_position), 1)),
                                     ])
        stacked_feature = np.vstack([stacked_feature,
                                     np.zeros((max_sample_size - stacked_feature.shape[0], stacked_feature.shape[1]))])

        stacked_labs_with_feature.append(stacked_feature)

    stacked_labs_with_feature = np.array(stacked_labs_with_feature)
    return stacked_labs_with_feature


def read_f0s():
    max_f0_size = 0
    f0s = []
    for i in range(0, 71):
        f0_file_name = '{:0>2d}_f0.txt'.format(i)
        if not os.path.isfile(local_path + 'cn_gen/' + f0_file_name):
            continue
        with open(local_path + 'cn_gen/' + f0_file_name, 'r') as f0_file:
            lines = f0_file.readlines()
            lines = np.array(lines).astype(np.float)

            if len(lines) > max_f0_size:
                max_f0_size = len(lines)
            f0s.append(lines)

    # 即要生成的最多个f0，
    print(max_f0_size)

    for index, f0 in enumerate(f0s):
        f0s[index] = np.append(f0, np.zeros(max_f0_size - len(f0)))

    f0s = np.array(f0s)
    f0s = np.reshape(f0s, (f0s.shape[0], f0s.shape[1], 1))

    # (31, max_f0_size, 1)
    return f0s, max_f0_size


def features_add_f0(labs, f0s):
    result = np.zeros((labs.shape[0], labs.shape[1], labs.shape[2] + 1))
    for i in range(0, labs.shape[0]):
        result[i] = np.hstack([labs[i], f0s[i]])
    return result


def read_sp():
    max_sp_size = 0
    sps = []
    for i in range(0, 10):
        sp_file_name  = '{:0>2d}_sp.txt'.format(i)

        if not os.path.isfile(local_path + 'cn_gen/' + sp_file_name):
            continue
        with open(local_path + 'cn_gen/' + sp_file_name, 'r') as sp_file:
            lines = sp_file.readlines()
            lines = np.array(lines)
            new_lines = []
            for line in lines:
                new_lines.append(np.array(line.split(',')).astype(float))
            new_lines = np.array(new_lines)
            if len(lines) > max_sp_size:
                max_sp_size = len(lines)
            sps.append(new_lines)
            print(len(sps))

    # 即要生成的最多个sp，
    print(max_sp_size)

    for index, sp in enumerate(sps):
        try:
            sps[index]=np.vstack([sps[index], np.zeros((max_sp_size-len(sp),num_of_sp))])
        except:
            print(index)
    sps = np.array(sps)
    return sps, max_sp_size

In [7]:
cn_labs=read_cn_labs()
# print(cn_labs[0][:10])
cn_labs = feature_expend(cn_labs)
cn_labs = sp_feature_extract(cn_labs)
f0s, max_f0_size = read_f0s()
cn_labs = features_add_f0(cn_labs, f0s)

max sample size: 8898


8898


In [8]:
sps, _ = read_sp()

1


2


KeyboardInterrupt: 

In [231]:
sps=np.array(sps)
sps2=np.zeros(sps.shape)
max_sp_size=8898

for index, sp in enumerate(sps):
    try:
        sps2[index]=np.vstack([sps[index], np.zeros((max_sp_size-len(sp),513))])
    except: 
        print(sps[index].shape,np.zeros((max_sp_size-len(sp),1025)).shape)

(8898, 513) (0, 1025)
(7555, 513) (1343, 1025)
(7425, 513) (1473, 1025)
(7602, 513) (1296, 1025)
(6787, 513) (2111, 1025)
(6500, 513) (2398, 1025)
(6975, 513) (1923, 1025)
(7127, 513) (1771, 1025)
(7665, 513) (1233, 1025)


In [9]:
def wavenetBlock(n_atrous_filters, atrous_filter_size, dilation_rate):
    def f(input_):
        residual = input_
        tanh_out = Conv1D(n_atrous_filters, atrous_filter_size,
                          dilation_rate=dilation_rate,
                          padding='causal',

                          activation='tanh')(input_)
        sigmoid_out = Conv1D(n_atrous_filters, atrous_filter_size,
                             dilation_rate=dilation_rate,
                             padding='causal',
                             activation='sigmoid')(input_)
        merged = Multiply()([tanh_out, sigmoid_out])
        skip_out = Conv1D(1, 1, activation='relu', padding='same')(merged)
        out = Add()([skip_out, residual])
        return out, skip_out

    return f


def get_basic_generative_model(input_dim):
    input_ = Input(shape=(input_dim, 1))
    A, B = wavenetBlock(64, 2, 2)(input_)
    skip_connections = [B]
    for i in range(20):
        A, B = wavenetBlock(64, 2, 2 ** ((i + 2) % 9))(A)
        skip_connections.append(B)
    net = Add()(skip_connections)
    net = Activation('relu')(net)
    net = Convolution1D(1, 1, activation='relu')(net)
    net = Convolution1D(1, 1)(net)
    net = Flatten()(net)
    # net = Dense(32, activation='relu')(net)
    net = Dense( math.ceil(num_of_sp/20), activation='linear')(net)
    model = Model(input=input_, output=net)
    # model.compile(loss='categorical_crossentropy', optimizer='sgd',
    #               metrics=['accuracy'])
    model.compile(loss='mse', optimizer=Adam(lr=0.0001),
                  metrics=['accuracy'])
    model.summary()
    return model


def frame_generator(total_frame, input_data_size, frame_shift, control_input, minibatch_size=20):
    X = []
    y = []
    while 1:

        for lab_file_index in range(0, len(total_frame)):
            total_frame_len = len(total_frame[lab_file_index])
            X = []
            y = []
            for cold_start_index in range(0, input_data_size):
                # frame = np.zeros((input_data_size - cold_start_index, 103))

                frame = total_frame[lab_file_index][:cold_start_index]
                new_frame = []
                for i in range(len(frame)):
                    temp = frame[i]
                    temp = [0.00000000001 if i==0 else i for i in temp]
                    temp = np.log(temp)
                    # temp = np.fft.irfft(temp)
                    # temp = temp[:NUM_OUT_PUT]
                    # temp = np.fft.rfft(temp)
                    temp = np.array([i for index, i in enumerate(temp) if index % 20 == 0])
                    temp = -np.round(temp)
                    new_frame.append(temp)
                frame = np.array(new_frame)
                frame = np.append(np.zeros((input_data_size - cold_start_index,  math.ceil(num_of_sp/20))),
                                  frame)

                # frame = np.append(frame.flatten(), total_frame[lab_file_index][:cold_start_index].flatten())
                frame = np.append(frame.flatten(), control_input[lab_file_index][cold_start_index])

                # X.append(frame.reshape((input_data_size+ control_input.shape[2], 1)))
                X.append(frame.reshape((frame.shape[0], 1)))
                # print(frame.reshape((frame.shape[0], 1)).shape)
                temp = total_frame[lab_file_index][cold_start_index]
                
                temp = [0.00000000001 if i==0 else i for i in temp]
                temp = np.log(temp)
                temp = np.array([i for index, i in enumerate(temp) if index % 20 == 0])
                temp = -np.round(temp)
                
                # temp = np.fft.irfft(temp)
                # temp = temp[:NUM_OUT_PUT]
                # temp = np.fft.rfft(temp)
                y.append(temp)
                # print(temp.shape)
                if len(X) == minibatch_size:
                    yield np.array(X), np.array(y)
                    X = []
                    y = []

            for i in range(0, total_frame_len - input_data_size - 1, frame_shift):

                # 获取一帧 (input_data_size, num_of_sp)
                frame = total_frame[lab_file_index][i:i + input_data_size]

                # print(frame.shape)
                # print(frame.shape)

                new_frame = []
                for j in range(len(frame)):
                    temp = frame[j]
                    temp = [0.00000000001 if i==0 else i for i in temp]
                    temp = np.log(temp)
                    temp = np.array([i for index, i in enumerate(temp) if index % 20 == 0])
                    temp = -np.round(temp)
                    # temp = np.fft.irfft(temp)
                    # temp = temp[:NUM_OUT_PUT]
                    # temp = np.fft.rfft(temp)
                    new_frame.append(temp)
                frame = np.array(new_frame)

                if len(frame) < input_data_size:
                    break

                if i + input_data_size >= total_frame_len:
                    break

                # 获取该帧 frame 后面的那个sample
                temp = total_frame[lab_file_index][i + input_data_size]
                temp = [0.00000000001 if i==0 else i for i in temp]
                temp = np.log(temp)
                temp = np.array([i for index, i in enumerate(temp) if index % 20 == 0])
                temp = -np.round(temp)
                # temp = [0.00000000001 if i==0 else i for i in temp]
                # temp = np.log(temp) 
                # temp = np.fft.irfft(temp)
                # temp = temp[:NUM_OUT_PUT]
                # temp = np.fft.rfft(temp)
                # (1,num_of_sp)? 
                # target_val = int(temp)

                # frame.shape = (64,1)

                # Control Input
                frame = np.append(frame.flatten(), control_input[lab_file_index][i + input_data_size])
                # X值即前一帧
                X.append(frame.reshape((frame.shape[0], 1)))
                # print(frame.reshape((frame.shape[0], 1)).shape)
                y.append(temp)
                # print(temp.shape)

                # 获取一个mini-batch的数据返回
                if len(X) == minibatch_size:
                    yield np.array(X), np.array(y)
                    X = []
                    y = []


def f0_generate(model, f0_window_size, input_size, control_input):
    print('Generating audio...')
    new_f0s = np.zeros(max_f0_size)
    seed_audio = np.zeros(f0_window_size)
    curr_sample_idx = 0
    while curr_sample_idx < new_f0s.shape[0]:
        seed = np.append(seed_audio, control_input[curr_sample_idx])

        Y = np.array(model.predict(seed.reshape(1, input_size, 1)
                                   ), dtype=float)

        new_f0s[curr_sample_idx] = Y
        seed_audio[:-1] = seed_audio[1:]

        seed_audio[-1] = Y

        # percent
        # pc_str = str(round(100 * curr_sample_idx / float(new_audio.shape[0]), 2))
        # sys.stdout.write('Percent complete: ' + pc_str + '\r')
        # sys.stdout.flush()
        curr_sample_idx += 1
        if curr_sample_idx % int(new_f0s.shape[0] / 10) == 0:
            print(curr_sample_idx / int(new_f0s.shape[0] / 10))
    print('Audio generated.')
    return new_f0s.astype(np.int16)


def sp_generate(model, sp_window_size, input_size, control_input):
    print('Generating audio...')
    MAX_SP_SIZE = 7000
    new_sps = np.zeros((MAX_SP_SIZE, math.ceil(num_of_sp/20)))

    seed_audio = np.zeros((sp_window_size, math.ceil(num_of_sp/20)))
    curr_sample_idx = 0
    while curr_sample_idx < new_sps.shape[0]:
        seed = np.append(seed_audio.flatten(), control_input[curr_sample_idx])
        Y = np.array(model.predict(seed.reshape(1, input_size, 1)
                                   ), dtype=float)

        new_sps[curr_sample_idx] = Y
        # seed_audio = seed_audio[:-1]
        # seed_audio[:-1] = seed_audio[1:]
        # seed_audio[-1] = Y
        # seed_audio = Y
        
        curr_sample_idx += 1
        if curr_sample_idx % int(new_sps.shape[0] / 10) == 0:
            print(curr_sample_idx / int(new_sps.shape[0] / 10))

    print('Audio generated.')
    return new_sps.astype(np.int16)


In [10]:
n_epochs = 2000
input_data_size = 0
frame_shift = 1

# model = get_basic_generative_model(input_data_size+labs.shape[2])
# (65713-control_input_size)/1025 = input_data_size: 64
model = get_basic_generative_model(input_data_size*len(np.fft.rfft(np.zeros(20)))+num_of_features)
# model = load_model(local_path+"sp_model_2.h5")
training_data_gen = frame_generator(sps[0:29], input_data_size, frame_shift, 
                                    cn_labs[0:29])
validation_data_gen = frame_generator(sps[1:2], input_data_size, frame_shift, 
                                      cn_labs[1:2])

# model.fit_generator(training_data_gen, samples_per_epoch=100, nb_epoch=n_epochs,
#                     validation_data=validation_data_gen, nb_val_samples=500, verbose=1,
#                     callbacks=[TensorBoard(log_dir='./tmp/log', histogram_freq=0, write_graph=True,
#                                           write_images=True)])

model.fit_generator(training_data_gen, samples_per_epoch=5000, nb_epoch=n_epochs,
                     nb_val_samples=500, verbose=1,
                    callbacks=[TensorBoard(log_dir='./tmp/log', histogram_freq=0, write_graph=True,
                                          write_images=True)])

/Users/Zizy/anaconda/envs/tensorflow/lib/python3.5/site-packages/ipykernel_launcher.py:35: UserWarning: Update your `Model` call to the Keras 2 API: `Model(outputs=Tensor("de..., inputs=Tensor("in...)`


__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 179, 1)       0                                            
__________________________________________________________________________________________________
conv1d_1 (Conv1D)               (None, 179, 64)      192         input_1[0][0]                    
__________________________________________________________________________________________________
conv1d_2 (Conv1D)               (None, 179, 64)      192         input_1[0][0]                    
__________________________________________________________________________________________________
multiply_1 (Multiply)           (None, 179, 64)      0           conv1d_1[0][0]                   
                                                                 conv1d_2[0][0]                   
__________

/Users/Zizy/anaconda/envs/tensorflow/lib/python3.5/site-packages/ipykernel_launcher.py:22: UserWarning: The semantics of the Keras 2 argument `steps_per_epoch` is not the same as the Keras 1 argument `samples_per_epoch`. `steps_per_epoch` is the number of batches to draw from the generator at each epoch. Basically steps_per_epoch = samples_per_epoch/batch_size. Similarly `nb_val_samples`->`validation_steps` and `val_samples`->`steps` arguments have changed. Update your method calls accordingly.
/Users/Zizy/anaconda/envs/tensorflow/lib/python3.5/site-packages/ipykernel_launcher.py:22: UserWarning: Update your `fit_generator` call to the Keras 2 API: `fit_generator(<generator..., callbacks=[<keras.ca..., steps_per_epoch=5000, epochs=2000, validation_steps=500, verbose=1)`


Epoch 1/2000


   1/5000 [..............................] - ETA: 1:31:42 - loss: 1348.3000 - acc: 0.0000e+00

...

1365/5000 [=======>......................] - ETA: 6:56 - loss: 61.6096 - acc: 0.3037

1366/5000 [=======>......................] - ETA: 6:56 - loss: 61.5818 - acc: 0.3036

1367/5000 [=======>......................] - ETA: 6:56 - loss: 61.5777 - acc: 0.3034

1368/5000 [=======>......................] - ETA: 6:55 - loss: 61.6071 - acc: 0.3032

KeyboardInterrupt: 

In [12]:
model.save(local_path+'cn_model.h5')

In [56]:
import re
from pypinyin import pinyin, lazy_pinyin, Style
import copy

def pinyin_normalize(input):
    result = re.sub(r'([yjqx])u', r'\1v', input)
    result = re.sub(r'iu', 'iou', result)
    result = re.sub(r'ui', 'uei', result)
    result = re.sub(r'un', 'uen', result)
    result = re.sub(r'yi', r'i', result)
    result = re.sub(r'wu', r'u', result)
    result = re.sub(r'^y', 'i', result)
    result = re.sub(r'^w', 'u', result)
    return result


def pinyin_search(input):
    phos = ["b", "p", "m", "f", "d", "t", "n", "l", "g", "k", "h", "j", "q", "x", "zh", "ch", "sh", "r", "z", "c", "s",
            "i", "u", "v", "a", "o", "e", "ai", "ei", "ao", "ou", "an", "en", "ang", "eng", "ong", "ia", "ua", "uo",
            "ie", "ve", "uai", "uei", "iao", "iou", "ian", "uan", "van", "in", "uen", "vn", "iang", "uang", "ing",
            "ueng", "iong", "er"]
    for i in phos:
        if re.match(r'' + input, i):
            return True
    return False


def pinyin_split(input_pinyin):
    input_pinyin = pinyin_normalize(input_pinyin)
    result = []
    i = 0
    j = 1
    while True:

        if pinyin_search(input_pinyin[i:j]) > 0 and j <= len(input_pinyin):
            j += 1
        else:
            sub = input_pinyin[i:j - 1]
            result.append(sub)
            i = j - 1
            j = i + 1

        if i >= len(input_pinyin):
            break
    return result


def sentence_split(sentence):
    pinyins = pinyin(sentence, style=Style.NORMAL)
    splited = [pinyin_split(p[0]) for p in pinyins]
    return splited


def change_lab(lab_index, phos):
    _cn_labs=read_cn_labs()[lab_index]
    
    idx = 0
    result = copy.copy(_cn_labs)
    for index, frame in enumerate(_cn_labs):
        if frame['cur_pho'] != 'pau':
            result[index]['cur_pho'] = phos[idx]
            idx += 1
            if idx>=len(phos):
                break
                
    _cn_labs = feature_expend([_cn_labs])
    _cn_labs = sp_feature_extract(_cn_labs)
    _f0s, _ = read_f0s()
    print(_cn_labs.shape,np.array([_f0s[lab_index]]).shape)
    _cn_labs = features_add_f0(_cn_labs, np.array([_f0s[lab_index]]))
    return _cn_labs[0]

In [57]:
import array

phos = [x for y in sentence_split('你好吗我很好我是一个好孩子') for x in y]
new_labs = change_lab(0,phos)


max sample size: 8898


8898
(1, 8898, 178) (1, 8898, 1)


['n', 'i', 'h', 'ao', 'm', 'a', 'uo', 'h', 'en', 'h', 'ao', 'uo', 'sh', 'i', 'i', 'g', 'e', 'h', 'ao', 'h', 'ai', 'z', 'i']


In [62]:
new_sps = sp_generate(model,input_data_size,input_data_size*math.ceil(num_of_sp/20)+num_of_features,cn_labs[0])

from scipy import interpolate 

sps_cp = copy.copy(new_sps)
new_sps2=np.zeros((7000,num_of_sp))
for sps_index in range(len(sps_cp)):
    _sps =sps_cp[sps_index] 
    f = interpolate.interp1d(np.array(range(0, len(_sps))), _sps, kind='slinear')
    sp2 = f(np.arange(0,len(_sps)-1,(len(_sps)-1)/num_of_sp))
    sp2=np.exp(-sp2)
    new_sps2[sps_index] = sp2

with open(local_path+"new_sps_cn_ori.txt",'w',encoding='utf-8') as f:
    for i in range(0,len(new_sps2)):
        for j in range(len(new_sps2[i])):
            f.write(str(new_sps2[i][j])+",")
        f.write("\r\n")

Generating audio...


1.0


2.0


3.0


4.0


...

6.0


7.0


8.0


9.0


10.0
Audio generated.


In [61]:
with open(local_path+"new_sps_cn_.txt",'w',encoding='utf-8') as f:
    for i in range(0,len(new_sps2)):
        for j in range(len(new_sps2[i])):
            f.write(str(new_sps2[i][j])+",")
        f.write("\r\n")